# Veri Analizleri

In [74]:
import pandas as pd
import numpy as np
from scipy import stats

In [75]:
from plotly import express
from plotly import graph_objects
from plotly import io

io.templates.default = "plotly_dark"

In [76]:
from statsmodels.formula.api import ols
from statsmodels.stats.anova import anova_lm
from statsmodels.tsa.stattools import adfuller, acf, breakvar_heteroskedasticity_test

In [77]:
from statsmodels.graphics import tsaplots
import matplotlib.pyplot as plt

In [78]:
import plotly.graph_objects as go
import statsmodels.api as sm 

In [79]:
country_name = ["France", "Greece",	"Italy", "Portugal", "Spain", "Türkiye"]

In [80]:
sheet = [i for i in range(2,10)]
sheet

[2, 3, 4, 5, 6, 7, 8, 9]

In [90]:
df_3 = pd.read_excel("OECD VERİLERİ ELİF BAĞCI TEZ V0_python.xlsx", sheet_name=2 )
df_3.columns[1]

'Current expenditure on health, % of gross domestic product'

In [83]:
def create_corr_plot(series, plot_pacf=False):
    corr_array = pacf(series.dropna(), alpha=0.05) if plot_pacf else acf(series.dropna(), alpha=0.05)
    lower_y = corr_array[1][:,0] - corr_array[0]
    upper_y = corr_array[1][:,1] - corr_array[0]

    fig = go.Figure()
    [fig.add_scatter(x=(x,x), y=(0,corr_array[0][x]), mode='lines',line_color='#3f3f3f') 
     for x in range(len(corr_array[0]))]
    fig.add_scatter(x=np.arange(len(corr_array[0])), y=corr_array[0], mode='markers', marker_color='#1f77b4',
                   marker_size=12)
    fig.add_scatter(x=np.arange(len(corr_array[0])), y=upper_y, mode='lines', line_color='rgba(255,255,255,0)')
    fig.add_scatter(x=np.arange(len(corr_array[0])), y=lower_y, mode='lines',fillcolor='rgba(32, 146, 230,0.3)',
            fill='tonexty', line_color='rgba(255,255,255,0)')
    fig.update_traces(showlegend=False)
    fig.update_xaxes(range=[-1,13])
    fig.update_yaxes(zerolinecolor='#000000')
    
    title='Partial Autocorrelation (PACF)' if plot_pacf else 'Autocorrelation (ACF)'
    fig.update_layout(title=title)
    fig.show()

In [91]:
for i in sheet:
    df_2 = pd.read_excel("OECD VERİLERİ ELİF BAĞCI TEZ V0_python.xlsx", sheet_name=i )
    print("###########################")
    print(df_2.columns[1], end="\n\n")
    print("###########################")
    df_2 = pd.read_excel("OECD VERİLERİ ELİF BAĞCI TEZ V0_python.xlsx", sheet_name=i, header=1 )

    for country in country_name:
        print("###########################")
        print(f"{country}'nin Zaman Serisi Analizi")
        print("###########################")

        trendlin = express.scatter(
            df_2,
            x="t",
            y=f"{country}",
            title=f"{country}'s Current expenditure on health, % of gross domestic product",
            trendline = "ols"
        )

        trendlin.show()
        linear_model = ols(f"{country} ~ t", data=df_2).fit()
        print(linear_model.summary())
        print(" ", end="\n")
        print("###########################")
        print("Verinin Durağanlık Kontrolü", end="\n\n")
        print("H0: Seri durağan değildir.")
        print("H1: Seri durağandır.", end="\n\n")
        adfullerx = adfuller(df_2[[f"{country}"]])
        print(f'Test Stat = {round(adfullerx[0], 4)}, p-value = {round(adfullerx[1], 4)}')

        if adfullerx[1]<0.05:
            print("p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Yani seri durağandır.")
        elif adfullerx[1]>0.05:
            print("p-value 0.05'ten büyüktür. H0 hipotezi reddedilememiştir. Yani seri durağan değildir.", end="\n\n")
        print("###########################")
        print("Hataların Normal Dağılması", end="\n\n")
        residual_values = linear_model.resid

        print("H0: Normal dağılım varsayımı sağlanmaktadır.")
        print("H1: Normal dağılım varsayımı sağlanmamaktadır.", end="\n\n")

        test_stat, pvalue = stats.shapiro(residual_values)
        print(f'Test Stat = {round(test_stat, 4)}, p-value = {round(pvalue, 4)}')
        if pvalue<0.05:
            print("p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar normal dağılmamıştır.")
        elif pvalue>0.05:
            print("p-value 0.05'ten büyüktür. H0 hipotezi reddedilememiştir. Yani hatalar normal dağılmıştır.", end="\n\n")
        hist = express.histogram(residual_values, title="Hataların Dağılımı")
        hist.show()

        print("###########################")
        print("Hataların Rassallığı", end="\n\n")

        print("     Hataların Durağanlığı", end="\n\n")

        adfullery = adfuller(residual_values)
        print(f'Test Stat = {round(adfullery[0], 4)}, p-value = {round(adfullery[1], 4)}')

        if adfullery[1]<0.05:
            print("p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar durağandır.")
        elif adfullery[1]>0.05:
            print("p-value 0.05'ten büyüktür. H0 hipotezi reddedilememiştir. Yani hatalar durağan değildir.", end="\n\n")

        resid_scatter = express.scatter(
            df_2,
            x="t",
            y=residual_values,
            title="Hataların Rassallığı"
        )

        resid_scatter.show()


        print("     Hataların Otokorelasyonu", end="\n\n")

        print("Ljung-Box q istatistiğinin Hipotezleri")
        print("H0: Veriler bağımsız (random) olarak dağılmıştır.")
        print("H1: Veriler bağımsız (random) olarak dağılmamıştır.", end="\n\n")

        acf_df = pd.DataFrame(pd.DataFrame(acf(residual_values, qstat=True)).T)
        acf_df.columns = ["ACF", "Ljung-Box q statistic", "p-value"]
        display(acf_df[1:6])

        create_corr_plot(residual_values)


###########################
Current expenditure on health, % of gross domestic product

###########################
###########################
France'nin Zaman Serisi Analizi
###########################


                            OLS Regression Results                            
Dep. Variable:                 France   R-squared:                       0.832
Model:                            OLS   Adj. R-squared:                  0.823
Method:                 Least Squares   F-statistic:                     93.96
Date:                Tue, 31 Jan 2023   Prob (F-statistic):           8.67e-09
Time:                        18:47:11   Log-Likelihood:                -3.4373
No. Observations:                  21   AIC:                             10.87
Df Residuals:                      19   BIC:                             12.96
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      9.6921      0.136     71.484      0.0

###########################
Hataların Rassallığı

     Hataların Durağanlığı

Test Stat = -3.2538, p-value = 0.0171
p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar durağandır.


     Hataların Otokorelasyonu

Ljung-Box q istatistiğinin Hipotezleri
H0: Veriler bağımsız (random) olarak dağılmıştır.
H1: Veriler bağımsız (random) olarak dağılmamıştır.



ACF  Ljung-Box q statistic   p-value
1  0.424596               4.762776  0.092422
2  0.126839               4.784537  0.188272
3  0.028477               4.845543  0.303516
4 -0.046338               5.683216  0.338273
5 -0.166580               6.781309  0.341546

...

###########################
Türkiye'nin Zaman Serisi Analizi
###########################


                            OLS Regression Results                            
Dep. Variable:                Türkiye   R-squared:                       0.776
Model:                            OLS   Adj. R-squared:                  0.764
Method:                 Least Squares   F-statistic:                     65.85
Date:                Tue, 31 Jan 2023   Prob (F-statistic):           1.36e-07
Time:                        18:47:15   Log-Likelihood:                -89.269
No. Observations:                  21   AIC:                             182.5
Df Residuals:                      19   BIC:                             184.6
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     98.1974      8.077     12.157      0.0

###########################
Hataların Rassallığı

     Hataların Durağanlığı

Test Stat = -4.0121, p-value = 0.0013
p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar durağandır.


     Hataların Otokorelasyonu

Ljung-Box q istatistiğinin Hipotezleri
H0: Veriler bağımsız (random) olarak dağılmıştır.
H1: Veriler bağımsız (random) olarak dağılmamıştır.



ACF  Ljung-Box q statistic   p-value
1  0.538856               7.012465  0.030010
2 -0.002294               9.751095  0.020805
3 -0.319469              15.407331  0.003927
4 -0.446185              18.179059  0.002730
5 -0.303013              18.222435  0.005700

# Interrupted Time Series for Türkiye

    Yukarıda referans ülkelerin ve Türkiye'nin zaman serisi regresyon analizi sonuçlarına bakılırken, bu kısımdan itibaren Türkiye için interrupted time series analysis yapılmıştır.

In [86]:
trendlin = express.scatter(
        df_2,
        x="t",
        y= "Türkiye",
        title="Türkiye's Current expenditure on health, % of gross domestic product",
    )

trendlin.add_trace(
go.Scatter(
    x = [1,5],
    y = [analys.predict()[0], analys.predict()[4]],
)
 )   

trendlin.add_trace(
go.Scatter(
    x = [5,6],
    y = [analys.predict()[4], analys.predict()[5]]
)

 )

trendlin.add_trace(
go.Scatter(
    x = [6,21],
    y = [analys.predict()[5], analys.predict()[20]]
)

 )  

trendlin.show() 

X = df_2[["t", "interruption", "interrupted t"]]
y = df_2["Türkiye"]

X = sm.add_constant(X) 
analys= sm.OLS(y, X).fit()
print(analys.summary())

print("###########################")
print("Hataların Normal Dağılması", end="\n\n")
residual_values = analys.resid
print("H0: Normal dağılım varsayımı sağlanmaktadır.")
print("H1: Normal dağılım varsayımı sağlanmamaktadır.", end="\n\n")
test_stat, pvalue = stats.shapiro(residual_values)
print(f'Test Stat = {round(test_stat, 4)}, p-value = {round(pvalue, 4)}')
if pvalue<0.05:
    print("p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar normal dağılmamıştır.")
elif pvalue>0.05:
     print("p-value 0.05'ten büyüktür. H0 hipotezi reddedilememiştir. Yani hatalar normal dağılmıştır.", end="\n\n")
hist = express.histogram(residual_values, title="Hataların Dağılımı")
hist.show()
print("###########################")
print("Hataların Rassallığı", end="\n\n")
print("     Hataların Durağanlığı", end="\n\n")
adfullery = adfuller(residual_values)
print(f'Test Stat = {round(adfullery[0], 4)}, p-value = {round(adfullery[1], 4)}')
if adfullery[1]<0.05:
    print("p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar durağandır.")
elif adfullery[1]>0.05:
    print("p-value 0.05'ten büyüktür. H0 hipotezi reddedilememiştir. Yani hatalar durağan değildir.", end="\n\n")
resid_scatter = express.scatter(
    df_2,
    x="t",
    y=residual_values,
    title="Hataların Rassallığı"
)
resid_scatter.show()
print("     Hataların Otokorelasyonu", end="\n\n")
print("Ljung-Box q istatistiğinin Hipotezleri")
print("H0: Veriler bağımsız (random) olarak dağılmıştır.")
print("H1: Veriler bağımsız (random) olarak dağılmamıştır.", end="\n\n")
acf_df = pd.DataFrame(pd.DataFrame(acf(residual_values, qstat=True)).T)
acf_df.columns = ["ACF", "Ljung-Box q statistic", "p-value"]
display(acf_df[1:6])
create_corr_plot(residual_values)

                            OLS Regression Results                            
Dep. Variable:                Türkiye   R-squared:                       0.622
Model:                            OLS   Adj. R-squared:                  0.555
Method:                 Least Squares   F-statistic:                     9.310
Date:                Tue, 31 Jan 2023   Prob (F-statistic):           0.000721
Time:                        18:42:40   Log-Likelihood:               -0.46516
No. Observations:                  21   AIC:                             8.930
Df Residuals:                      17   BIC:                             13.11
Df Model:                           3                                         
Covariance Type:            nonrobust                                         
                    coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------------------------
const             4.6710      0.288     16.197

###########################
Hataların Rassallığı

     Hataların Durağanlığı

Test Stat = -3.0095, p-value = 0.034
p-value 0.05'ten küçüktür. H0 hipotezi reddedilmiştir. Hatalar durağandır.


     Hataların Otokorelasyonu

Ljung-Box q istatistiğinin Hipotezleri
H0: Veriler bağımsız (random) olarak dağılmıştır.
H1: Veriler bağımsız (random) olarak dağılmamıştır.



ACF  Ljung-Box q statistic   p-value
1  0.522704               6.728984  0.034580
2  0.071711               7.490489  0.057803
3 -0.168461              11.047677  0.026033
4 -0.353838              15.363202  0.008918
5 -0.378097              17.746058  0.006899

In [ ]:
grafik = express.line(x=[i+1 for i in range(len(analys.predict()))], y =analys.predict(), markers=True)
grafik.show()